# Test CopernicusReadAwsStacTask

We would need to install .aws/config profile with copernicus credentials for this to work on each machine.

In [1]:
from dotenv import load_dotenv

load_dotenv(".env")

True

In [2]:
from odc.loader._rio import configure_s3_access
import boto3

configure_s3_access(cloud_defaults=True)
client = boto3.client("s3")

In [3]:
import logging

# set std out
logging.basicConfig(
    level=logging.DEBUG, format="%(asctime)s %(levelname)s [%(name)s] %(message)s"
)

In [4]:
import os

print("CDSE key set?", bool(os.getenv("CDSE_AWS_ACCESS_KEY_ID")))
print("CDSE secret set?", bool(os.getenv("CDSE_AWS_SECRET_ACCESS_KEY")))

CDSE key set? True
CDSE secret set? True


In [5]:
from src.task import copernicus_read_env
from pathlib import Path
from dep_tools.searchers import PystacSearcher
from dep_tools.loaders import OdcLoader
import src.utils as utils
from src.task import CopernicusReadAwsStacTask

from dep_tools.grids import PACIFIC_GRID_10

tile_ids = [(63, 21)]
# processor = utils.VegProcessor()

catalog = "https://stac.dataspace.copernicus.eu/v1"
collection = "sentinel-2-global-mosaics"
datetime = "2024-04-01"

2025-12-03 05:49:52,642 DEBUG [fiona.env] GDAL data found in package: path='/usr/local/lib/python3.10/dist-packages/fiona/gdal_data'.
2025-12-03 05:49:52,646 DEBUG [fiona.env] PROJ data found in package: path='/usr/local/lib/python3.10/dist-packages/fiona/proj_data'.
2025-12-03 05:49:52,666 DEBUG [botocore.hooks] Changing event name from creating-client-class.iot-data to creating-client-class.iot-data-plane
2025-12-03 05:49:52,671 DEBUG [botocore.hooks] Changing event name from before-call.apigateway to before-call.api-gateway
2025-12-03 05:49:52,682 DEBUG [botocore.hooks] Changing event name from request-created.machinelearning.Predict to request-created.machine-learning.Predict
2025-12-03 05:49:52,686 DEBUG [botocore.hooks] Changing event name from before-parameter-build.autoscaling.CreateLaunchConfiguration to before-parameter-build.auto-scaling.CreateLaunchConfiguration
2025-12-03 05:49:52,689 DEBUG [botocore.hooks] Changing event name from before-parameter-build.route53 to before-

In [6]:
processor = utils.VegProcessorKeepNonVegPixels()

2025-12-03 05:50:56,634 INFO [src.utils] Loaded referenced mean: [[[80.05354792]]

 [[90.66337282]]

 [[74.55025903]]]
2025-12-03 05:50:56,637 INFO [src.utils] Loaded referenced std: [[[44.24210402]]

 [[39.65290116]]

 [[30.30396384]]]


In [7]:
from odc.geo.geobox import GeoBox
import geopandas as gpd

test_area = gpd.read_file("Gn_D4DInsights_Fiji_AOI_small_test_3832_251203.geojson")
geobox = GeoBox.from_bbox(test_area.total_bounds, crs=3832, resolution=10)

In [8]:
searcher = PystacSearcher(
    catalog=catalog,
    collections=[collection],
    datetime=datetime,
)


loader = OdcLoader(
    bands=["B04", "B03", "B02", "observations"],  # , "B08"],
    chunks={"x": 1024, "y": 1024},
)

2025-12-03 05:50:57,142 DEBUG [urllib3.util.retry] Converted retries value: 5 -> Retry(total=5, connect=None, read=None, redirect=None, status=None)
2025-12-03 05:50:57,147 DEBUG [urllib3.util.retry] Converted retries value: 5 -> Retry(total=5, connect=None, read=None, redirect=None, status=None)
2025-12-03 05:50:57,153 DEBUG [pystac_client.stac_api_io] GET https://stac.dataspace.copernicus.eu/v1 Headers: {'User-Agent': 'python-requests/2.32.5', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive'}
2025-12-03 05:50:57,169 DEBUG [urllib3.connectionpool] Starting new HTTPS connection (1): stac.dataspace.copernicus.eu:443
2025-12-03 05:50:58,562 DEBUG [urllib3.connectionpool] https://stac.dataspace.copernicus.eu:443 "GET /v1 HTTP/1.1" 200 948


In [9]:
items = searcher.search(geobox)
# Check this is working
print(f"Found {len(items)} items")

2025-12-03 05:50:58,801 DEBUG [pystac_client.stac_api_io] GET https://stac.dataspace.copernicus.eu/v1/ Headers: {'User-Agent': 'python-requests/2.32.5', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive'}
2025-12-03 05:50:59,132 DEBUG [urllib3.connectionpool] https://stac.dataspace.copernicus.eu:443 "GET /v1/ HTTP/1.1" 200 948
2025-12-03 05:50:59,139 DEBUG [pystac_client.stac_api_io] POST https://stac.dataspace.copernicus.eu/v1/search Headers: {'User-Agent': 'python-requests/2.32.5', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive', 'Content-Length': '195', 'Content-Type': 'application/json'} Payload: {"bbox": [177.74608451754284, -17.462374746224885, 177.78022049833936, -17.436766450589595], "datetime": "2024-04-01T00:00:00Z/2024-04-01T23:59:59Z", "collections": ["sentinel-2-global-mosaics"]}
2025-12-03 05:50:59,601 DEBUG [urllib3.connectionpool] https://stac.dataspace.copernicus.eu:443 "POST /v1/search HTTP/1.1" 200 2207


Found 1 items


In [9]:
all_items = list(items)

In [23]:
item = all_items[0]

In [27]:
item.to_dict()

{'type': 'Feature',
 'stac_version': '1.1.0',
 'stac_extensions': ['https://cs-si.github.io/eopf-stac-extension/v1.2.0/schema.json',
  'https://stac-extensions.github.io/alternate-assets/v1.2.0/schema.json',
  'https://stac-extensions.github.io/authentication/v1.1.0/schema.json',
  'https://stac-extensions.github.io/eo/v2.0.0/schema.json',
  'https://stac-extensions.github.io/file/v2.1.0/schema.json',
  'https://stac-extensions.github.io/processing/v1.2.0/schema.json',
  'https://stac-extensions.github.io/product/v1.0.0/schema.json',
  'https://stac-extensions.github.io/storage/v2.0.0/schema.json',
  'https://stac-extensions.github.io/timestamps/v1.1.0/schema.json'],
 'id': 'Sentinel-2_mosaic_2024_Q2_60KWF_0_0',
 'geometry': {'type': 'Polygon',
  'coordinates': [[[176.9998109807786, -18.089070484917123],
    [176.99981192147922, -17.184449999102682],
    [177.9409106163382, -17.182255923868265],
    [177.9456158580422, -18.086753352908964],
    [176.9998109807786, -18.089070484917123]]

In [9]:
from odc.loader._rio import configure_rio
from task import get_copernicus_rio_config
import rasterio


aws, boto_session, gdal_opts = get_copernicus_rio_config()

2025-12-03 05:23:19,940 DEBUG [task] Using copernicus profile
2025-12-03 05:23:19,942 DEBUG [botocore.hooks] Changing event name from creating-client-class.iot-data to creating-client-class.iot-data-plane
2025-12-03 05:23:19,947 DEBUG [botocore.hooks] Changing event name from before-call.apigateway to before-call.api-gateway
2025-12-03 05:23:19,950 DEBUG [botocore.hooks] Changing event name from request-created.machinelearning.Predict to request-created.machine-learning.Predict
2025-12-03 05:23:19,953 DEBUG [botocore.hooks] Changing event name from before-parameter-build.autoscaling.CreateLaunchConfiguration to before-parameter-build.auto-scaling.CreateLaunchConfiguration
2025-12-03 05:23:19,967 DEBUG [botocore.hooks] Changing event name from before-parameter-build.route53 to before-parameter-build.route-53
2025-12-03 05:23:19,969 DEBUG [botocore.hooks] Changing event name from request-created.cloudsearchdomain.Search to request-created.cloudsearch-domain.Search
2025-12-03 05:23:19,970

In [12]:
boto_session.get_credentials()

In [10]:
with rasterio.Env(session=aws, **gdal_opts):
    configure_rio(cloud_defaults=True, aws={"session": boto_session}, **gdal_opts)
    data = loader.load(items, geobox)
    meta = utils.extract_raster_meta(data)
    output = processor.process(data)

2025-12-03 05:23:20,072 DEBUG [rasterio.env] Entering env context: <rasterio.env.Env object at 0x75bbd192bbe0>
2025-12-03 05:23:20,075 DEBUG [rasterio.env] Starting outermost env
2025-12-03 05:23:20,077 DEBUG [rasterio.env] No GDAL environment exists
2025-12-03 05:23:20,078 DEBUG [rasterio.env] New GDAL environment <rasterio._env.GDALEnv object at 0x75bbdc1b5ab0> created
2025-12-03 05:23:20,082 DEBUG [rasterio._filepath] Installing FilePath filesystem handler plugin...
2025-12-03 05:23:20,092 DEBUG [rasterio._env] GDAL data found in package: path='/usr/local/lib/python3.10/dist-packages/rasterio/gdal_data'.
2025-12-03 05:23:20,094 DEBUG [rasterio._env] PROJ data found in package: path='/usr/local/lib/python3.10/dist-packages/rasterio/proj_data'.
2025-12-03 05:23:20,095 DEBUG [rasterio._env] Started GDALEnv: self=<rasterio._env.GDALEnv object at 0x75bbdc1b5ab0>.
2025-12-03 05:23:20,096 DEBUG [rasterio.env] Entered env context: <rasterio.env.Env object at 0x75bbd192bbe0>
2025-12-03 05:23

IndexError: index 3 is out of bounds for axis 0 with size 3

In [15]:
processor.tce_img

xarray.core.dataset.Dataset

In [11]:
# land_shp = utils.download_and_extract_land_polygons()


for tile_id in tile_ids:
    print(tile_id)
    geobox = PACIFIC_GRID_10.tile_geobox(tile_id)

    searcher = PystacSearcher(
        catalog=catalog,
        collections=[collection],
        datetime=datetime,
    )

    loader = OdcLoader(
        bands=["B04", "B03", "B02", "observations"],  # , "B08"],
        chunks={"x": 1024, "y": 1024},
    )

    items = searcher.search(geobox)
    # Check this is working
    print(f"Found {len(items)} items")
    with rasterio.Env(session=aws, **gdal_opts):
        configure_rio(cloud_defaults=True, aws={"session": boto_session}, **gdal_opts)
        data = loader.load(items, geobox)
        meta = utils.extract_raster_meta(data)
        output = processor.process(data)

2025-12-03 05:26:07,060 DEBUG [urllib3.util.retry] Converted retries value: 5 -> Retry(total=5, connect=None, read=None, redirect=None, status=None)
2025-12-03 05:26:07,064 DEBUG [urllib3.util.retry] Converted retries value: 5 -> Retry(total=5, connect=None, read=None, redirect=None, status=None)
2025-12-03 05:26:07,067 DEBUG [pystac_client.stac_api_io] GET https://stac.dataspace.copernicus.eu/v1 Headers: {'User-Agent': 'python-requests/2.32.5', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive'}
2025-12-03 05:26:07,069 DEBUG [urllib3.connectionpool] Starting new HTTPS connection (1): stac.dataspace.copernicus.eu:443


(63, 21)


2025-12-03 05:26:08,376 DEBUG [urllib3.connectionpool] https://stac.dataspace.copernicus.eu:443 "GET /v1 HTTP/1.1" 200 948
2025-12-03 05:26:08,411 DEBUG [pystac_client.stac_api_io] GET https://stac.dataspace.copernicus.eu/v1/ Headers: {'User-Agent': 'python-requests/2.32.5', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive'}
2025-12-03 05:26:08,707 DEBUG [urllib3.connectionpool] https://stac.dataspace.copernicus.eu:443 "GET /v1/ HTTP/1.1" 200 948
2025-12-03 05:26:08,711 DEBUG [pystac_client.stac_api_io] POST https://stac.dataspace.copernicus.eu/v1/search Headers: {'User-Agent': 'python-requests/2.32.5', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive', 'Content-Length': '192', 'Content-Type': 'application/json'} Payload: {"bbox": [177.380649859963, -17.65281330691017, 178.24303253271773, -16.824114445989782], "datetime": "2024-04-01T00:00:00Z/2024-04-01T23:59:59Z", "collections": ["sentinel-2-global-mosaics"]}
2025-12-03 05:2

Found 4 items


2025-12-03 05:30:29,479 DEBUG [botocore.hooks] Changing event name from creating-client-class.iot-data to creating-client-class.iot-data-plane
2025-12-03 05:30:29,484 DEBUG [botocore.hooks] Changing event name from before-call.apigateway to before-call.api-gateway
2025-12-03 05:30:29,487 DEBUG [botocore.hooks] Changing event name from request-created.machinelearning.Predict to request-created.machine-learning.Predict
2025-12-03 05:30:29,489 DEBUG [botocore.hooks] Changing event name from before-parameter-build.autoscaling.CreateLaunchConfiguration to before-parameter-build.auto-scaling.CreateLaunchConfiguration
2025-12-03 05:30:29,490 DEBUG [botocore.hooks] Changing event name from before-parameter-build.route53 to before-parameter-build.route-53
2025-12-03 05:30:29,491 DEBUG [botocore.hooks] Changing event name from request-created.cloudsearchdomain.Search to request-created.cloudsearch-domain.Search
2025-12-03 05:30:29,493 DEBUG [botocore.hooks] Changing event name from docs.*.autosc

IndexError: index 3 is out of bounds for axis 0 with size 3

In [ ]:
savestem = f"cloudless_{str(tile_id).replace(',', '_')}_{datetime.replace('-','')}_land"

utils.save_raster(
    processor.img,
    meta,
    save_path=Path(f"/data/{savestem}.tif"),
    nbits=8,
    overwrite=True,
)
utils.save_raster(
    processor.tce_img,
    meta,
    save_path=Path(f"/data/{savestem}.tif"),
    nbits=8,
    overwrite=True,
)
utils.save_raster(
    processor.mask.astype("uint8"),
    meta,
    save_path=Path(f"/data/landmask_{savestem}.tif"),
    nbits=8,
    overwrite=True,
)
utils.save_raster(
    output["height"],
    meta,
    save_path=Path(f"/data/height_{savestem}.tif"),
    nbits=None,
    overwrite=True,
)
utils.save_raster(
    output["average_observations"], meta, f"/data/conf_{savestem}.tif", overwrite=True
)

In [ ]:
task = CopernicusReadAwsStacTask(
    itempath="s3://dep-sentinel-test/deptest",
    id="smoke",
    area=geobox,
    searcher=searcher,  # returns Copernicus-hosted items
    loader=loader,  # opens /vsis3/ urls
    processor=processor,
)

paths = task.run()
print(paths)

In [ ]:
for tile_id in tile_ids:
    print(tile_id)

    searcher = PystacSearcher(
        catalog=catalog,
        collections=[collection],
        datetime=datetime,
    )

    loader = OdcLoader(
        bands=["B04", "B03", "B02", "observations"],  # , "B08"],
        chunks={"x": 1024, "y": 1024},
    )

    items = searcher.search(geobox)
    # Check this is working
    print(f"Found {len(items)} items")
    with copernicus_read_env(profile="copernicus", force_keys=True) as env:
        print(env)
        task = CopernicusReadAwsStacTask(
            itempath="s3://dep-sentinel-test/deptest",
            id="smoke",
            area=geobox,
            searcher=searcher,  # returns Copernicus-hosted items
            loader=loader,  # opens /vsis3/ urls
            processor=processor,
        )